# Notebook for doing analysis of paleo biomarker data

The steps are as follows:

- Read in the excel file
- Remove upwelling cores
- Apply filters based on methane index and GDGTrs
- Select COLUMNS to process
- Separate data in to low & mid latitude vs. high latitude
- Run Lo(w)ess to calculate data for all ages
- Calculate gradients between low & mid latitudes and high latitudes

In [39]:
from loguru import logger
from pathlib import Path
from typing import List, Tuple, Optional
import numpy as np
import pandas as pd
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import plotly.express as px
import paleos.interpolate as pin

from utils import filter_mi, filter_gdgtrs, filter_cren, filter_bit_ringstetra
from utils import fill_nans, apply_filters
from utils import filter_data


Define our data locations

In [40]:
input_path = Path("data", "input")
output_path = Path("data", "gradients")
if not output_path.exists():
    output_path.mkdir()


Read the main excel file and set the age as the index after converting it to a float (decimals)

In [41]:
df = pd.read_excel(
    input_path / "Table S2_SST compilation.xlsx", sheet_name=0, skiprows=[1]
)
df["Age (Ma)"] = df["Age (Ma)"].astype(float)
df = df.set_index("Age (Ma)")
df = df.sort_index()


Read in comparison d15N gradient data

In [42]:
df_resample = pd.read_csv(input_path / "d15N_A_P_gradient.csv", index_col=0)
resample_gradient = df_resample["Gradient"]


Set some options to work with

- exclusion thresholds
- smoothing
- ages to drop
- columns to process
- plotting ranges
- clipping

Current favourite uses a LOESS with a smoothing factor of 0.02 and time step of 0.2

In [43]:
# # FILTERS TO APPLY
FILTERS = [filter_mi, filter_gdgtrs, filter_cren]
# FILTERS = [filter_mi, filter_gdgtrs, filter_cren, filter_bit_ringstetra]

# SITES TO EXCLUDE
SITES_TO_EXCLUDE = []

# SMOOTHING
# SMOOTHING_METHOD = "LOWESS"
SMOOTHING_METHOD = "LOESS"
SMOOTHING_FACTOR = 0.02
TIME_STEP = 0.2
OUTPUT_AGES = np.arange(0, 57.5, TIME_STEP)

# AGES TO DROP BEFORE SMOOTHING
EXCLUDE_AGES_BEFORE_SMOOTHING = False
TO_EXCLUDE = []

# AGES TO DROP FROM FINAL RESULT
NAN_AGES = True
AGES_TO_NAN = [[0.2, 4.4], [17.6, 22.5], [30.9, 31.7]]

# COLUMNS TO PROCESS & PLOTTING RANGES
COLUMNS = [
    "TEX",
    "SSTH (°C)",
    "SST Bayspar (°C)",
    "Bayspar 5th (°C)",
    "Bayspar 95th (°C)",
]
PLOT_RANGE = [-5, 30]
# COLUMNS = ["TEX"]
# PLOT_RANGE = [-0.05, 0.4]

# CLIP GRADIENTS
CLIP_GRADIENTS = False
MIN_GRADIENT = -5
MAX_GRADIENT = 25


Fill some NaN values with -999 to help select data points later

Restrict by conditions on:

1. MI < mi_threshold
2. %GDGTrs < gdgtrs_threshold
3. Cren' > cren_threshold
4. Filtered MI < mi_threshold and %GDGTrs < gdgtrs_threshold and Cren' > cren_threshold

In [44]:
df = fill_nans(df)
filtered, postpend = apply_filters(df, FILTERS)
filtered.to_csv(output_path / f"filtered{postpend}.csv")
# compare to filter data
logger.info("Check individual filtering versus the original function")
chk = filter_data(df)


2022-07-14 23:01:07.761 | INFO     | utils:filter_mi:42 - Filtering on methane index < 0.4
2022-07-14 23:01:07.763 | INFO     | utils:filter_mi:43 - number of rows pre filter = 5170
2022-07-14 23:01:07.773 | INFO     | utils:filter_mi:45 - number of rows post filter = 5006
2022-07-14 23:01:07.775 | INFO     | utils:filter_gdgtrs:51 - Filtering on GDGTRS < 30
2022-07-14 23:01:07.776 | INFO     | utils:filter_gdgtrs:52 - number of rows pre filter = 5006
2022-07-14 23:01:07.782 | INFO     | utils:filter_gdgtrs:54 - number of rows post filter = 4800
2022-07-14 23:01:07.784 | INFO     | utils:filter_cren:60 - Filtering on CREN > 1000
2022-07-14 23:01:07.786 | INFO     | utils:filter_cren:61 - number of rows pre filter = 4800
2022-07-14 23:01:07.792 | INFO     | utils:filter_cren:63 - number of rows post filter = 4782
2022-07-14 23:01:08.155 | INFO     | __main__:<cell line: 5>:5 - Check individual filtering versus the original function
2022-07-14 23:01:08.157 | INFO     | utils:filter_data:

Now do the following with some diagnostic plots

- Separate data in to low & mid latitude vs. high latitude
- Run Lo(w)ess to calculate data for all ages
- Calculate gradients between low & mid latitudes and high latitudes

In [45]:
def plot_data(
    fig,
    data: pd.DataFrame,
    COLUMNS: List[str],
    color: str,
    group: str,
    mode: str = "lines+markers",
):
    for idx, col in enumerate(COLUMNS):
        fig.add_trace(
            go.Scatter(
                x=data.index,
                y=data[col],
                mode=mode,
                legendgroup=group,
                name=col,
                line=dict(color=color),
            ),
            row=idx + 1,
            col=1,
        )
    return fig


Now have our selection criteria, want to move ahead with other analyses. Will use:

- Core locations not marked as upwellings
- no conditions and filtered conditions
- TEXH and Bayspar using averaged paleolat

Begin by removing things we are not interested in

In [46]:
def remove_sites(df: pd.DataFrame) -> pd.DataFrame:
    """Remove specified sites from the data"""
    logger.info(f"Removing sites {SITES_TO_EXCLUDE}")
    return df[~df["Site"].isin(SITES_TO_EXCLUDE)]


def remove_subpolar(df: pd.DataFrame) -> pd.DataFrame:
    """Remove the transition latitude category from the data"""
    logger.info("Removing latitude category 'transition'")
    return df[df["Latitude category"] != "transition"]


original = df.copy()
original = remove_sites(original)
original = remove_subpolar(original)

filtered = remove_sites(filtered)
filtered = remove_subpolar(filtered)


2022-07-14 23:01:08.470 | INFO     | __main__:remove_sites:3 - Removing sites []
2022-07-14 23:01:08.478 | INFO     | __main__:remove_subpolar:9 - Removing latitude category 'transition'
2022-07-14 23:01:08.484 | INFO     | __main__:remove_sites:3 - Removing sites []
2022-07-14 23:01:08.491 | INFO     | __main__:remove_subpolar:9 - Removing latitude category 'transition'


Make a plot of the original data to help qc the data

In [47]:
fig = px.scatter(
    df.dropna(subset=["Latitude category"]),
    # y="SSTH",
    y="SST Bayspar (°C)",
    color="Latitude category",
    hover_data=[
        "Site",
        "TEX",
        "SSTH (°C)",
        "SST Bayspar (°C)",
        "MI",
        "%GDGTrs",
        "Cren'",
        "Reference",
        "Age-adjusted paleolatitude",
        "Latitude category",
    ],
)
fig.update_layout(
    title_text=f"SST points",
    height=800,
    xaxis_title="Age (Ma)",
    yaxis_title="Temperature (C)",
)
fig.update_xaxes(range=[0, 60])
fig.update_yaxes(range=[-5, 50])
fig.show()


Separate out latitude categories

- Low and mid latitude are one set
- High latitude is the other set

In [48]:
def separate_latitudes(df: pd.DataFrame) -> Tuple[pd.DataFrame, pd.DataFrame]:
    """Separate low and mid latitudes from high latitudes"""
    low_and_mid = df[df["Latitude category"].isin(["low latitude", "mid latitude"])]
    high = df[df["Latitude category"] == "high latitude"]
    return low_and_mid, high


original_low_and_mid, original_high = separate_latitudes(original)
filtered_low_and_mid, filtered_high = separate_latitudes(filtered)


Exclude some age ranges before doing the smoothing

In [49]:
def remove_excluded_ages(
    df: pd.DataFrame, ages_to_exclude: List[float]
) -> pd.DataFrame:
    """Remove any specified age ranges from the data"""
    logger.info(f"Removing age ranges {ages_to_exclude}")
    for exclude_section in ages_to_exclude:
        logger.info(f"Removing points in time section {exclude_section}")
        df = df[(df.index < exclude_section[0]) | (df.index > exclude_section[1])]
    return df


if EXCLUDE_AGES_BEFORE_SMOOTHING:
    logger.info("Excluding ages before smoothing")
    filtered_high = remove_excluded_ages(filtered_high, TO_EXCLUDE)


In [50]:
def plot_lats(
    fig,
    low_and_mid: pd.DataFrame,
    high: pd.DataFrame,
    COLUMNS: List[str],
    mode: str = "lines+markers",
):
    for idx, col in enumerate(COLUMNS):
        fig.add_trace(
            go.Scatter(
                x=low_and_mid.index,
                y=low_and_mid[col],
                mode=mode,
                legendgroup="Low and mid",
                name=col,
                line=dict(color="orange"),
            ),
            row=idx + 1,
            col=1,
        )
        fig.add_trace(
            go.Scatter(
                x=high.index,
                y=high[col],
                mode=mode,
                legendgroup="High",
                name=col,
                line=dict(color="blue"),
            ),
            row=idx + 1,
            col=1,
        )
        fig.add_trace(
            go.Scatter(
                x=[17.6, 17.6],
                y=[high[col].min(), low_and_mid[col].max()],
                mode="lines",
                line=dict(color="red"),
            ),
            row=idx + 1,
            col=1,
        )
    return fig


Plot the separate latitudes for the original dataset with no data removal based on Methane Index and GDGTrs

In [51]:
fig = make_subplots(
    rows=len(COLUMNS),
    cols=1,
    shared_xaxes=True,
    subplot_titles=COLUMNS,
    vertical_spacing=0.05,
)
fig = plot_lats(fig, original_low_and_mid, original_high, COLUMNS)
fig.update_layout(height=1200)
fig.show()


Plot the separate latitudes for data restricted by thresholds on Methane Index and GDGTrs

In [52]:
fig = make_subplots(
    rows=len(COLUMNS),
    cols=1,
    shared_xaxes=True,
    subplot_titles=COLUMNS,
    vertical_spacing=0.05,
)
fig = plot_lats(fig, filtered_low_and_mid, filtered_high, COLUMNS)
fig.update_layout(height=1200)
fig.show()


Now apply the Lowess and calculate the gradient for the original data and sanitise data (by Methane Index and GDGTrs)

In [53]:
def lowess_run(
    series: pd.Series,
    smoothing_factor: float,
    output_ages: np.ndarray,
    method: str = "LOWESS",
) -> pd.Series:
    series = series.dropna()
    if method.lower() == "lowess":
        logger.info("Using LOWESS with statsmodels")
        output = pin.lowess_sm_interpolate(series, output_ages, smoothing_factor)
    elif method.lower() == "loess":
        logger.info("Using LOESS with external function")
        output = pin.loess_ext_interpolate(series, output_ages, smoothing_factor)
    else:
        raise ValueError(f"Unknown method {method}")
    return output


def lowess_gradient(
    low_and_mid: pd.DataFrame,
    high: pd.DataFrame,
    smoothing_factor,
    output_ages: np.ndarray,
    columns: List[str],
    method: str = "LOWESS",
) -> pd.DataFrame:
    # get the output ages
    data = []
    for col in columns:
        # get lowess for low and mid latitudes
        low_and_mid_lowess = lowess_run(
            low_and_mid[col], smoothing_factor, output_ages, method=method
        )
        # get lowess for high latitudes
        high_lowess = lowess_run(
            high[col], smoothing_factor, output_ages, method=method
        )
        # calculate gradients
        gradient = low_and_mid_lowess - high_lowess
        col_df = pd.DataFrame(
            data={
                f"{col} Low Mid {SMOOTHING_METHOD}": low_and_mid_lowess,
                f"{col} High {SMOOTHING_METHOD}": high_lowess,
                f"{col} Gradient": gradient,
            }
        )
        data.append(col_df)
    return pd.concat(data, axis=1)


# all the data
original_gradients = lowess_gradient(
    original_low_and_mid,
    original_high,
    SMOOTHING_FACTOR,
    OUTPUT_AGES,
    COLUMNS,
    method=SMOOTHING_METHOD,
)
# filtered data
filtered_gradients = lowess_gradient(
    filtered_low_and_mid,
    filtered_high,
    SMOOTHING_FACTOR,
    OUTPUT_AGES,
    COLUMNS,
    method=SMOOTHING_METHOD,
)


2022-07-14 23:01:10.999 | INFO     | __main__:lowess_run:12 - Using LOESS with external function
2022-07-14 23:01:11.001 | INFO     | paleos.interpolate:loess_ext_interpolate:312 - Series size 2733, smoothing factor 0.02, points = 54
2022-07-14 23:01:11.152 | INFO     | __main__:lowess_run:12 - Using LOESS with external function
2022-07-14 23:01:11.153 | INFO     | paleos.interpolate:loess_ext_interpolate:312 - Series size 1013, smoothing factor 0.02, points = 20
2022-07-14 23:01:11.245 | INFO     | __main__:lowess_run:12 - Using LOESS with external function
2022-07-14 23:01:11.246 | INFO     | paleos.interpolate:loess_ext_interpolate:312 - Series size 2733, smoothing factor 0.02, points = 54
2022-07-14 23:01:11.463 | INFO     | __main__:lowess_run:12 - Using LOESS with external function
2022-07-14 23:01:11.464 | INFO     | paleos.interpolate:loess_ext_interpolate:312 - Series size 1015, smoothing factor 0.02, points = 20
2022-07-14 23:01:11.573 | INFO     | __main__:lowess_run:12 - Us

Do some post processing

In [54]:
def set_ages_to_nan(gradients: pd.DataFrame, ages_to_nan: np.ndarray) -> pd.DataFrame:
    """Set some ages to NaN values"""
    logger.info(f"Setting following ages to NaN {ages_to_nan}")
    for col in COLUMNS:
        for nan_section in ages_to_nan:
            gradients.loc[nan_section[0] : nan_section[1], f"{col} Gradient"] = np.nan
    return gradients


if NAN_AGES:
    logger.info("Setting some ages to NaN")
    original_gradients = set_ages_to_nan(original_gradients, AGES_TO_NAN)
    filtered_gradients = set_ages_to_nan(filtered_gradients, AGES_TO_NAN)

if CLIP_GRADIENTS:
    logger.info(f"Clipping gradients between {MIN_GRADIENT} and {MAX_GRADIENT}")
    for col in COLUMNS:
        gradient_col = f"{col} Gradient"
        original_gradients[gradient_col] = original_gradients[gradient_col].clip(
            lower=MIN_GRADIENT, upper=MAX_GRADIENT
        )
        filtered_gradients[gradient_col] = filtered_gradients[gradient_col].clip(
            lower=MIN_GRADIENT, upper=MAX_GRADIENT
        )


2022-07-14 23:01:13.065 | INFO     | __main__:<cell line: 10>:11 - Setting some ages to NaN
2022-07-14 23:01:13.067 | INFO     | __main__:set_ages_to_nan:3 - Setting following ages to NaN [[0.2, 4.4], [17.6, 22.5], [30.9, 31.7]]
2022-07-14 23:01:13.077 | INFO     | __main__:set_ages_to_nan:3 - Setting following ages to NaN [[0.2, 4.4], [17.6, 22.5], [30.9, 31.7]]


In [55]:
def plot_gradients(
    fig,
    df: pd.DataFrame,
    COLUMNS: List[str],
    mode: str = "lines+markers",
    compare: Optional[pd.Series] = None,
):
    for col in COLUMNS:
        col_name = f"{col} Gradient"
        col_data = df[col_name]
        fig.add_trace(go.Scatter(x=col_data.index, y=col_data, mode=mode, name=col))
    if compare is not None:
        fig.add_trace(
            go.Scatter(
                x=compare.index,
                y=compare,
                mode=mode,
                name="Nitrogen gradient",
                yaxis="y2",
            )
        )
    return fig


fig = go.Figure()
fig = plot_gradients(fig, original_gradients, COLUMNS, compare=resample_gradient)
fig.update_layout(
    title_text="Original",
    height=500,
    yaxis=dict(title=f"Biomarker gradient {SMOOTHING_METHOD}", range=PLOT_RANGE),
    yaxis2=dict(
        title="Nitrogen gradient resample",
        overlaying="y",
        side="right",
    ),
)
fig.show()

fig = go.Figure()
fig = plot_gradients(fig, filtered_gradients, COLUMNS, compare=resample_gradient)
fig.update_layout(
    title_text=f"Filtered",
    height=500,
    yaxis=dict(title=f"Biomarker gradient {SMOOTHING_METHOD}", range=PLOT_RANGE),
    yaxis2=dict(
        title="Nitrogen gradient resample",
        overlaying="y",
        side="right",
    ),
)
fig.show()


In [56]:
original_low_and_mid[COLUMNS].to_csv(
    output_path / f"{SMOOTHING_METHOD}_all_mid_and_low.csv"
)
original_high[COLUMNS].to_csv(output_path / f"{SMOOTHING_METHOD}_all_high.csv")
original_gradients.to_csv(output_path / f"{SMOOTHING_METHOD}_all_gradients.csv")

filtered_low_and_mid[COLUMNS].to_csv(
    output_path / f"{SMOOTHING_METHOD}{postpend}_mid_and_low.csv"
)
filtered_high[COLUMNS].to_csv(output_path / f"{SMOOTHING_METHOD}{postpend}_high.csv")
filtered_gradients.to_csv(output_path / f"{SMOOTHING_METHOD}{postpend}_gradients.csv")
